In [8]:
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd


### <공공 데이터셋에서 스팸과 스팸이 아닌 메일의 샘플을 내려 받아서 스팸 분류기를 만들어 보자>
#### 1. 데이터셋 내려받기

In [1]:
import os
import tarfile
import urllib

DOWNLOAD_ROOT = "http://spamassassin.apache.org/old/publiccorpus/"
HAM_URL = DOWNLOAD_ROOT + "20030228_easy_ham.tar.bz2"
SPAM_URL = DOWNLOAD_ROOT + "20030228_spam.tar.bz2"

In [2]:
print(HAM_URL, SPAM_URL)

http://spamassassin.apache.org/old/publiccorpus/20030228_easy_ham.tar.bz2 http://spamassassin.apache.org/old/publiccorpus/20030228_spam.tar.bz2


In [6]:
from google.colab import files
uploaded = files.upload()

Saving 20030228_easy_ham.tar.bz2 to 20030228_easy_ham.tar.bz2


In [7]:
files.upload()

Saving 20030228_spam.tar.bz2 to 20030228_spam.tar.bz2


{'20030228_spam.tar.bz2': b'BZh91AY&SYj\xc4\x8e$\x06-\x93\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xf3>\xddw\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xe3\xcc\xfdc\x0f<$3\x15S\xe8\x0c%\xf77Jo\xbb\xe3\xdf}\xf65W\xd5u\xc0D\x95\xda{\x96\xe6\xaag#U\xa8;f\x98r\xaaQ\x9dIv\xc0\xa7\x15\xd8\xe47;\xa4,\x02\xc7\xce\xdd\xb6R\xf7}\xef\x03\xdd\xddU(\xd73]\x001\xf6\xdcf\x8c\xf7\xd6\xd7\xd0\x00\x0f\x1e\x00z>\xeb\xa1\xefm}`/g\xae.]\xdb\xc0\x08@\x1b/\x00\x00\x17\x9c\xdc\xe2\xce\x97\x8fx\x0e\xf7u\xadp:(\xad\xdbs]6\x0e\xae\xed_`\x00\xd7\xc0\x00\xec\x00\x05\xec\x14\x00\x00\xf9\x00c\xd7\xbb*\x84\x00\ry\xd8T\x83\xa0\xda\xca\n}o]pt\xf2;\\N\xd0\xd5&\xc0em\xb9_Z^\x84|\xddO\x99\xa2fg\xbe{\x9b\xd93\xdd[\xddw\xbe-\x1e\xfa\xdf]>\xfb^\xcf\x81\xe7\xdd\xf5\xec\xd4!}\x9a\xd0\x17\x0er\xe9\xb2\xc8\xab\xe3w\xb0\xf5O\x8d\xc8\xe3\xeev\xdcuG\xb1\xbd4\xed\xb4\x0c\xf9=\xca\xb7\xce\x06y\xf6;\xb6\xf7\xde\xf7\xbe\xdd\xbe\xbd\xe9\xb5\xa56\xcd\xa6\xf7.\xce\xa9\x91RP^\xcbe \xdb\xdd\xbd\x1b\xb3\xe

In [27]:
import bz2

In [45]:
ham_data = bz2.open('/content/20030228_easy_ham.tar.bz2','rb')
spam_data = bz2.open('/content/20030228_spam.tar.bz2', 'rb')


In [46]:
spam = load_email(spam_data)

In [48]:
ham = load_email(ham_data)

In [50]:
ham_emails = [ham]
spam_emails = [spam]

In [53]:
print(ham.get_content().strip())

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [54]:
import os
import tarfile
import urllib

DOWNLOAD_ROOT = "http://spamassassin.apache.org/old/publiccorpus/"
HAM_URL = DOWNLOAD_ROOT + "20030228_easy_ham.tar.bz2"
SPAM_URL = DOWNLOAD_ROOT + "20030228_spam.tar.bz2"
SPAM_PATH = os.path.join("datasets", "spam")

def fetch_spam_data(spam_url=SPAM_URL, spam_path=SPAM_PATH):
    if not os.path.isdir(spam_path):
        os.makedirs(spam_path)
    for filename, url in (("ham.tar.bz2", HAM_URL), ("spam.tar.bz2", SPAM_URL)):
        path = os.path.join(spam_path, filename)
        if not os.path.isfile(path):
            urllib.request.urlretrieve(url, path)
        tar_bz2_file = tarfile.open(path)
        tar_bz2_file.extractall(path=SPAM_PATH)
        tar_bz2_file.close()

fetch_spam_data()

- 이번에 사용한 데이터는 내가 기존에 사용하던 데이터의 형태였던 csv, img, txt등 pandas로 읽을 수 있는 문서와 달랐다. 뿐만 아니라 내가 기존에 사용하던 데이터 로드 방식과 다른 방법으로 데이터를 받았다.
- 일단 ```os.makedirs(spam_path)```라는 방법으로 디렉토리를 만들어서 코드를 짜는 동시에 데이터를 로드 했다.
  - 그리고 이 파일이 bv2파일로, tarfile이라는 모듈을 import해야만 사용이 가능했었다.
  - 먼저 디렉토리를 이용해서 파일을 열고
  - 압축 파일이었기 때문에 압축을 풀기 위해서 ```file.extractall(path=SPAM_PATH)```로 또 한번 더 압축이 풀리면 저장될 디렉토리를 지정해 주었다.
  - 이후 ```file.close()```로 마무리를 해 주었다.

In [56]:
HAM_DIR = os.path.join(SPAM_PATH, 'easy_ham')
SPAM_DIR = os.path.join(SPAM_PATH,'spam')

#### 2. 데이터셋의 압축을 풀고 데이터 형식 실펴보기

In [57]:
ham_filename = [names for names in sorted(os.listdir(HAM_DIR))]
spam_filename = [names for names in sorted(os.listdir(SPAM_DIR))]

In [60]:
len(ham_filename), len(spam_filename)

(2501, 501)

In [61]:
import email
import email.policy

def load_email(is_spam, filename, spam_path=SPAM_PATH):
    directory = "spam" if is_spam else "easy_ham"
    with open(os.path.join(spam_path, directory, filename), "rb") as f:
        return email.parser.BytesParser(policy=email.policy.default).parse(f)

In [73]:
spam_email = [load_email(True, name, SPAM_PATH) for name in spam_filename]
ham_email = [load_email(None, name, SPAM_PATH) for name in ham_filename]

In [74]:
print(spam_email[0].get_content().strip())

<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.0 Transitional//EN">
<HTML><HEAD>
<META content="text/html; charset=windows-1252" http-equiv=Content-Type>
<META content="MSHTML 5.00.2314.1000" name=GENERATOR></HEAD>
<BODY><!-- Inserted by Calypso -->
<TABLE border=0 cellPadding=0 cellSpacing=2 id=_CalyPrintHeader_ rules=none 
style="COLOR: black; DISPLAY: none" width="100%">
  <TBODY>
  <TR>
    <TD colSpan=3>
      <HR color=black noShade SIZE=1>
    </TD></TR></TD></TR>
  <TR>
    <TD colSpan=3>
      <HR color=black noShade SIZE=1>
    </TD></TR></TBODY></TABLE><!-- End Calypso --><!-- Inserted by Calypso --><FONT 
color=#000000 face=VERDANA,ARIAL,HELVETICA size=-2><BR></FONT></TD></TR></TABLE><!-- End Calypso --><FONT color=#ff0000 
face="Copperplate Gothic Bold" size=5 PTSIZE="10">
<CENTER>Save up to 70% on Life Insurance.</CENTER></FONT><FONT color=#ff0000 
face="Copperplate Gothic Bold" size=5 PTSIZE="10">
<CENTER>Why Spend More Than You Have To?
<CENTER><FONT color=#ff0000 face="Copp

In [77]:
print(ham_email[0].get_content().strip())

Date:        Wed, 21 Aug 2002 10:54:46 -0500
    From:        Chris Garrigues <cwg-dated-1030377287.06fa6d@DeepEddy.Com>
    Message-ID:  <1029945287.4797.TMDA@deepeddy.vircio.com>


  | I can't reproduce this error.

For me it is very repeatable... (like every time, without fail).

This is the debug log of the pick happening ...

18:19:03 Pick_It {exec pick +inbox -list -lbrace -lbrace -subject ftp -rbrace -rbrace} {4852-4852 -sequence mercury}
18:19:03 exec pick +inbox -list -lbrace -lbrace -subject ftp -rbrace -rbrace 4852-4852 -sequence mercury
18:19:04 Ftoc_PickMsgs {{1 hit}}
18:19:04 Marking 1 hits
18:19:04 tkerror: syntax error in expression "int ...

Note, if I run the pick command by hand ...

delta$ pick +inbox -list -lbrace -lbrace -subject ftp -rbrace -rbrace  4852-4852 -sequence mercury
1 hit

That's where the "1 hit" comes from (obviously).  The version of nmh I'm
using is ...

delta$ pick -version
pick -- nmh-1.0.4 [compiled on fuchsia.cs.mu.OZ.AU at Sun Mar 17 14:55:56 

In [99]:
spam_email[33].get_content_type()
#.get_payload()를 이용하면 해당 이메일 내용을 불러올 수 있다.

'text/plain'

In [123]:
def count(word, counter):
  for i in word:
    temp = get_email_structure(i)
    if temp not in counter:
      counter[temp] = 0
    counter[temp] += 1
  return counter
#이 함수는 파이썬의 from collections import Counter의 모델을 대체할 수 있다.

#isinstance(file, shape)는 해당 파일의 형태가 나중에 주어진 변수와 일치하는지의 여부에 따라서 boolean값을 반환한다.
def get_email_structure(email):
  if isinstance(email, str):
    return email
  #이메일의 내용을 불러다줌
  data = email.get_payload()
  if isinstance(data, list):
    return 'Multipart:({})'.format(','.join([get_email_structure(sub_email) for sub_email in data]))
  else:
    return email.get_content_type()
  

In [124]:
def structure_check(email):
  counter = {}
  count(email, counter)
  return counter

In [125]:
structure_check(spam_email)

{'Multipart:(Multipart:(text/html))': 5,
 'Multipart:(Multipart:(text/html),application/octet-stream,image/jpeg)': 1,
 'Multipart:(Multipart:(text/plain,text/html),image/gif)': 1,
 'Multipart:(text/html)': 20,
 'Multipart:(text/html,application/octet-stream)': 2,
 'Multipart:(text/html,text/plain)': 1,
 'Multipart:(text/plain)': 19,
 'Multipart:(text/plain,application/octet-stream)': 1,
 'Multipart:(text/plain,image/jpeg)': 3,
 'Multipart:(text/plain,text/html)': 45,
 'multipart/alternative': 1,
 'text/html': 183,
 'text/plain': 219}

In [128]:
structure_check(ham_email)

{'Multipart:(Multipart:(text/plain,text/plain,text/plain),application/pgp-signature)': 1,
 'Multipart:(text/plain)': 3,
 'Multipart:(text/plain,Multipart:(text/plain))': 1,
 'Multipart:(text/plain,Multipart:(text/plain,text/plain),Multipart:(Multipart:(text/plain,application/x-pkcs7-signature)))': 1,
 'Multipart:(text/plain,Multipart:(text/plain,text/plain),text/rfc822-headers)': 1,
 'Multipart:(text/plain,application/ms-tnef,text/plain)': 1,
 'Multipart:(text/plain,application/octet-stream)': 2,
 'Multipart:(text/plain,application/pgp-signature)': 66,
 'Multipart:(text/plain,application/x-java-applet)': 1,
 'Multipart:(text/plain,application/x-pkcs7-signature)': 1,
 'Multipart:(text/plain,text/enriched)': 1,
 'Multipart:(text/plain,text/html)': 8,
 'Multipart:(text/plain,text/plain)': 4,
 'Multipart:(text/plain,video/mng)': 1,
 'text/plain': 2409}

- spam email과 ham email의 구성을 보게 된다면 spam의 경우에는 HTML데이터인 경우가 많고 ham의 경우에는 일반적인 텍스트가 더 많다.
- 그리고 ham 메일에는 pgp-signature이 있는데 spam메일에는 없다.

In [131]:
spam_email[0].items()

[('Return-Path', '<12a1mailbot1@web.de>'),
 ('Delivered-To', 'zzzz@localhost.spamassassin.taint.org'),
 ('Received',
  'from localhost (localhost [127.0.0.1])\tby phobos.labs.spamassassin.taint.org (Postfix) with ESMTP id 136B943C32\tfor <zzzz@localhost>; Thu, 22 Aug 2002 08:17:21 -0400 (EDT)'),
 ('Received',
  'from mail.webnote.net [193.120.211.219]\tby localhost with POP3 (fetchmail-5.9.0)\tfor zzzz@localhost (single-drop); Thu, 22 Aug 2002 13:17:21 +0100 (IST)'),
 ('Received',
  'from dd_it7 ([210.97.77.167])\tby webnote.net (8.9.3/8.9.3) with ESMTP id NAA04623\tfor <zzzz@spamassassin.taint.org>; Thu, 22 Aug 2002 13:09:41 +0100'),
 ('From', '12a1mailbot1@web.de'),
 ('Received',
  'from r-smtp.korea.com - 203.122.2.197 by dd_it7  with Microsoft SMTPSVC(5.5.1775.675.6);\t Sat, 24 Aug 2002 09:42:10 +0900'),
 ('To', 'dcek1a1@netsgo.com'),
 ('Subject', 'Life Insurance - Why Pay More?'),
 ('Date', 'Wed, 21 Aug 2002 20:31:57 -1600'),
 ('MIME-Version', '1.0'),
 ('Message-ID', '<0103c104200

In [132]:
spam_email[0]['Subject']

'Life Insurance - Why Pay More?'

#### 3. 테스트셋과 트레인셋으로 구분하기

In [134]:
from sklearn.model_selection import train_test_split
x,y = np.array(spam_email + ham_email), np.array([1]*len(spam_email)+[0]*len(ham_email))
x_train, x_test, y_train, y_test = train_test_split(x,y,test_size = 0.2)

#### 4. 전처리 함수 만들기

In [141]:
#우선 HTML파일을 txt파일로 바꿔주어야 한다.
#직접 전처리 함수를 만드는 것이 좋긴 하겠지만 그냥 BeautifulSoup 라이브러리를 이용하고자 한다.

In [140]:
import requests
from bs4 import BeautifulSoup

In [173]:
BeautifulSoup(html_spam_email[0].get_content())

<html>
<head>
<meta content="en-us" http-equiv="Content-Language"/>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="Microsoft FrontPage 4.0" name="GENERATOR"/>
<meta content="FrontPage.Editor.Document" name="ProgId"/>
<title>Would You Like to Save up to 80</title>
</head>
<body>
<div align="center">
<center>
<table bgcolor="#000080" border="0" height="83" width="469">
<tr>
<td align="center" bordercolor="#FFFFFF" height="48" width="100%"><font color="#FFFFFF" face="Tahoma" size="5"> Would You Like to
      <b> Save </b>up to<b> </b></font><b><font color="#FFFFCC" face="Tahoma" size="5">80%</font></b><font color="#FFFFFF" face="Tahoma" size="5">
      on <b>Printer</b>, </font><b><font color="#FF3300" face="Tahoma" size="5">Fax</font></b><font color="#FFFFFF" face="Tahoma" size="5">
      &amp; </font><b><font color="#FFFFCC" face="Tahoma" size="5"> Copier</font></b><font color="#FFFFFF" face="Tahoma" size="5"> Supplies?</font></td>
</tr>
</table>
</c

In [199]:
def change_to_txt(file):
  soup = BeautifulSoup(file)
  script_tag = soup.find_all(['script', 'style', 'header', 'footer', 'form'])
  for script in script_tag:
    script.extract()
  # 텍스트 단위 결합을 '\n'(줄바꿈)으로 함
  # 각 텍스트 단위의 시작과 끝에서 공백을 제거
  soup = soup.get_text(strip = True).split('\n')
  return soup


-  ```<head>``` 섹션을 삭제하고 모든 ```<a>``` 태그를 HYPERLINK 문자로 바꿉니다. 그런 다음 모든 HTML 태그를 제거하고 텍스트만 남깁니다. 보기 편하게 여러개의 개행 문자를 하나로 만들고 ```(&gt;나 &nbsp;``` 같은) html 엔티티를 복원한다.

|함수 |	값 또는 기능|
|----------|---------------|
re.compile(pattern)	| 패턴 문자열 pattern을 패턴 객체로 컴파일한다  
re.search(pattern, string)	|string에서 pattern과 매치하는 텍스트를 탐색한다 (임의 지점 매치)  
re.match(pattern, string) |	string에서 pattern과 매치하는 텍스트를 탐색한다 (시작점 매치)  
re.fullmatch(pattern, string)	| string에서 pattern과 매치하는 텍스트를 탐색한다 (전체 매치)  
re.sub(pattern, repl, string)	| string에서 pattern과 매치하는 텍스트를 repl로 치환한다  
re.split(pattern, string)	| string을 pattern을 기준으로 나눈다  

In [206]:
import re
from html import unescape
#unescape는 특수 문자를 일반 문자열로 바꿔주는 역할을 한다.
def html_to_plain_text(html):
    text = re.sub('<head.*?>.*?</head>', '', html, flags=re.M | re.S | re.I)
    text = re.sub('<a\s.*?>', ' HYPERLINK ', text, flags=re.M | re.S | re.I)
    text = re.sub('<.*?>', '', text, flags=re.M | re.S)
    text = re.sub(r'(\s*\n)+', '\n', text, flags=re.M | re.S)
    return unescape(text)

In [207]:
x_train[243].get_content()

'<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.0 Transitional//EN">\n<HTML><HEAD>\n</HEAD>\n<BODY bgColor=#cccccc topMargin=1>\n<DIV style="BACKGROUND: #e4e4e4; font-color: black"></DIV>\n<B><FONT face=Arial size=4>\n<A HREF="http://www.geocities.com/t_tricktvescort/ttrick.html">Click here to see the Bang Bus</A><br><br>It is wild!!!!!!\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br><br><br>\n<br><br>\n\ntepyycemkckiflbsvpcyi\n\n\n'

In [154]:
html_spam_email = [email for email in x_train[y_train==1] if get_email_structure(email) == 'text/html']


In [218]:
change_to_txt((html_spam_email[32].get_content()))

['HTML>İNTERNETTE KENDİNİZİ DAHA İYİ HİSSEDECEKSİNİZ.',
 "\t  İNGİLİZCE WEB SAYFALARININ TÜRKÇE'YE ÇEVİRİ YAZILIMI$ 39+KDVİNGİLİZCE'DEN TÜRKÇE'YE BİLGİSAYAR DESTEKLİ",
 '\t    METİN ÇEVİRİ YAZILIMI  ',
 '\t ',
 '\t (MS-WORD ALTINDA KULLANIM, TÜM WINDOWS VERSİYONLARI İLE UYUMLU)$ 69+KDVİKİ YAZILIM \xa0 BİRLİKTE$ ',
 '  89+KDVAyrıntılı Bilgi ',
 '      İçintıklayınBİLSAG Ltd.AHMET MİTHAT ',
 '      EFENDİ SOK. 22/1 ÇANKAYA 06700 / ANKARA /Tlf: 0312. 439 2850/ Fax: 0312. 439 9347bilsag@msn.com-------------------------------------------------------',
 'This sf.net email is sponsored by: OSDN - Tired of that same old',
 'cell phone?  Get a new here for FREE!',
 'https://www.inphonic.com/r.asp?r=sourceforge1']

In [213]:
html_to_plain_text((html_spam_email[32].get_content()))[:1000]

"HTML>\n   \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\n    İNTERNETTE KENDİNİZİ DAHA İYİ HİSSEDECEKSİNİZ.\n\t  İNGİLİZCE WEB SAYFALARININ TÜRKÇE'YE ÇEVİRİ YAZILIMI\n  $ 39+KDV\n     İNGİLİZCE'DEN TÜRKÇE'YE BİLGİSAYAR DESTEKLİ\n\t    METİN ÇEVİRİ YAZILIMI\n\t (MS-WORD ALTINDA KULLANIM, TÜM WINDOWS VERSİYONLARI İLE UYUMLU)\n  $ 69+KDV\n    İKİ YAZILIM \xa0 BİRLİKTE\n    $\n  89+KDV\n       HYPERLINK Ayrıntılı Bilgi\n      İçin\xa0   tıklayın\n      \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\n      \xa0 HYPERLINK\n      BİLSAG Ltd.\n      AHMET MİTHAT\n      EFENDİ SOK. 22/1 ÇANKAYA 06700 / ANKARA /\n      Tlf: 0312. 439 2850/ Fax: 0312. 439 9347\n       HYPERLINK bilsag@msn.com\n      \xa0\n      \xa0\nE-posta adres listemizden çıkmak içinÇIKAR tuşuna basınız\nBu elektronik posta: sitescooper-talk@example.sourceforge.net e gönderilmiştir\n-------------------------------------------------------\nThis sf.net email is sponsored by: OSDN - Tired of that same old\ncell phone?  Get a n

In [186]:
BeautifulSoup(html_spam_email[0].get_content())
#BeautifulSoup는 원래 웹크롤링을 할때에 많이 사용되는 라이브러리인데, 여기서 중요한 것은 이메일 데이터를 문자열로 바꿔준뒤에 텍스트 파일로 바꾸는 것이 가능하다는 것이다.

<html>
<head>
<meta content="en-us" http-equiv="Content-Language"/>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="Microsoft FrontPage 4.0" name="GENERATOR"/>
<meta content="FrontPage.Editor.Document" name="ProgId"/>
<title>Would You Like to Save up to 80</title>
</head>
<body>
<div align="center">
<center>
<table bgcolor="#000080" border="0" height="83" width="469">
<tr>
<td align="center" bordercolor="#FFFFFF" height="48" width="100%"><font color="#FFFFFF" face="Tahoma" size="5"> Would You Like to
      <b> Save </b>up to<b> </b></font><b><font color="#FFFFCC" face="Tahoma" size="5">80%</font></b><font color="#FFFFFF" face="Tahoma" size="5">
      on <b>Printer</b>, </font><b><font color="#FF3300" face="Tahoma" size="5">Fax</font></b><font color="#FFFFFF" face="Tahoma" size="5">
      &amp; </font><b><font color="#FFFFCC" face="Tahoma" size="5"> Copier</font></b><font color="#FFFFFF" face="Tahoma" size="5"> Supplies?</font></td>
</tr>
</table>
</c

- 이메일 데이터중에서 content라고 labeling되어 있는 부분만 이용할 것이기 때문에 그 부분만 추출해서 변형한느 함수를 만들어 보자.

In [236]:
def email_to_text(email):
    html = None
    for part in email.walk():
        ctype = part.get_content_type()
        if not ctype in ("text/plain", "text/html"):
            continue
        try:
            content = part.get_content()
        except: # in case of encoding issues
            content = str(part.get_payload())
        if ctype == "text/plain":
            return content
        else:
            html = content
    if html:
        return html_to_plain_text(html)

In [239]:
print(email_to_text(html_spam_email[32])[:100], "...")

HTML>
               
    İNTERNETTE KENDİNİZİ DAHA İYİ HİSSEDECEKSİNİZ.
	  İNGİLİZCE WEB SAYFALARIN ...


In [244]:
import google.colab
!pip install -q -U urlextract

In [245]:
#이메일 헤더 제거
import urlextract 
url_extractor = urlextract.URLExtract()
print(url_extractor.find_urls("Will it detect github.com and https://youtu.be/7Pq-S557XQU?t=3m32s"))

['github.com', 'https://youtu.be/7Pq-S557XQU?t=3m32s']


In [246]:
#소문자 변환
import nltk
stemmer = nltk.PorterStemmer()
for word in ("Computations", "Computation", "Computing", "Computed", "Compute", "Compulsive"):
  print(word, "=>", stemmer.stem(word))

Computations => comput
Computation => comput
Computing => comput
Computed => comput
Compute => comput
Compulsive => compuls


In [269]:

from sklearn.base import BaseEstimator, TransformerMixin
from collections import Counter

class EmailToWordCounterTransformer(BaseEstimator, TransformerMixin):
    def __init__(self, strip_headers=True, lower_case=True, remove_punctuation=True,
                 replace_urls=True, replace_numbers=True, stemming=True):
        self.strip_headers = strip_headers
        self.lower_case = lower_case
        self.remove_punctuation = remove_punctuation
        self.replace_urls = replace_urls
        self.replace_numbers = replace_numbers
        self.stemming = stemming
    def fit(self, X, y=None):
        return self
    def transform(self, X, y=None):
        X_transformed = []
        for email in X:
            text = email_to_text(email) or ""
            if self.lower_case:
                text = text.lower()
            if self.replace_urls and url_extractor is not None:
                urls = list(set(url_extractor.find_urls(text)))
                urls.sort(key=lambda url: len(url), reverse=True)
                #모든 URLs 주소를 'URL'로 대체
                for url in urls:
                    text = text.replace(url, " URL ")
            #모든 숫자를 'NUMBER'로 대체
            if self.replace_numbers:
                text = re.sub(r'\d+(?:\.\d*(?:[eE]\d+))?', 'NUMBER', text)
            if self.remove_punctuation:
                text = re.sub(r'\W+', ' ', text, flags=re.M)
            word_counts = Counter(text.split())
            #어간 추출
            if self.stemming and stemmer is not None:
                stemmed_word_counts = Counter()
                for word, count in word_counts.items():
                    stemmed_word = stemmer.stem(word)
                    stemmed_word_counts[stemmed_word] += count
                word_counts = stemmed_word_counts
            X_transformed.append(word_counts)
        return np.array(X_transformed)

In [251]:
x_few = x_train[:3]
x_few_wordcounts = EmailToWordCounterTransformer().fit_transform(x_few)
x_few_wordcounts

array([Counter({'the': 8, 'spamassassin': 7, 'list': 5, 'number': 5, 'are': 5, 'url': 4, 'devel': 4, 'contrib': 3, 'msquadrat': 3, 'de': 3, 'sourceforg': 3, 'net': 3, 'thi': 3, 'to': 3, 'you': 3, 'chang': 2, 'cc': 2, 'from': 2, 'i': 2, 'will': 2, 'be': 2, 'rule': 2, 'and': 2, 'instal': 2, 'on': 2, 'time': 2, 'mail': 2, 'assigne': 2, 'for': 2, 'bug': 2, 'or': 2, 'watch': 2, 'is': 2, 'what': 1, 'remov': 1, 'ad': 1, 'assignedto': 1, 'addit': 1, 'comment': 1, 'm': 1, 'gonna': 1, 'fix': 1, 'one': 1, 'think': 1, 'best': 1, 'solut': 1, 'copi': 1, 'modifi': 1, 'blib': 1, 'them': 1, 'there': 1, 'then': 1, 'file': 1, 'build': 1, 'not': 1, 'too': 1, 'receiv': 1, 'becaus': 1, 'someon': 1, 'who': 1, 'email': 1, 'sponsor': 1, 'by': 1, 'thinkgeek': 1, 'welcom': 1, 'geek': 1, 'heaven': 1, '_______________________________________________': 1}),
       Counter({'the': 30, 'to': 15, 'of': 12, 'and': 9, 'in': 9, 'are': 6, 'point': 5, 'yer': 5, 'it': 5, 's': 4, 'be': 4, 'is': 4, 'rather': 4, 'polit': 4, 'i

#### 5. 이메일을 벡터로 변환하는 함수를 만든다.

In [253]:
from scipy.sparse import csr_matrix

class WordCounterToVectorTransformer(BaseEstimator, TransformerMixin):
    def __init__(self, vocabulary_size=1000):
        self.vocabulary_size = vocabulary_size
    def fit(self, X, y=None):
        total_count = Counter()
        for word_count in X:
            for word, count in word_count.items():
                total_count[word] += min(count, 10)
        most_common = total_count.most_common()[:self.vocabulary_size]
        self.most_common_ = most_common
        self.vocabulary_ = {word: index + 1 for index, (word, count) in enumerate(most_common)}
        return self
    def transform(self, X, y=None):
        rows = []
        cols = []
        data = []
        for row, word_count in enumerate(X):
            for word, count in word_count.items():
                rows.append(row)
                cols.append(self.vocabulary_.get(word, 0))
                data.append(count)
        return csr_matrix((data, (rows, cols)), shape=(len(X), self.vocabulary_size + 1))
vocab_transformer = WordCounterToVectorTransformer(vocabulary_size=10)
x_few_vectors = vocab_transformer.fit_transform(x_few_wordcounts)
x_few_vectors

<3x11 sparse matrix of type '<class 'numpy.longlong'>'
	with 27 stored elements in Compressed Sparse Row format>

In [255]:
x_few_vectors.toarray()

array([[ 97,   8,   5,   3,   0,   2,   5,   0,   4,   7,   2],
       [266,  30,   2,  15,  12,   9,   6,   9,   0,   0,   4],
       [ 54,   8,   9,   3,   4,   1,   0,   1,   5,   0,   1]],
      dtype=int64)

In [256]:
from sklearn.pipeline import Pipeline

real_pipeline = Pipeline([
  ('email_to_word', EmailToWordCounterTransformer()),
  ('word_to_vector', WordCounterToVectorTransformer())                      
])

x_train = real_pipeline.fit_transform(x_train)

In [257]:
from sklearn.linear_model import SGDClassifier
sgd_clf = SGDClassifier(random_state = 42)
sgd_clf.fit(x_train, y_train)

SGDClassifier(alpha=0.0001, average=False, class_weight=None,
              early_stopping=False, epsilon=0.1, eta0=0.0, fit_intercept=True,
              l1_ratio=0.15, learning_rate='optimal', loss='hinge',
              max_iter=1000, n_iter_no_change=5, n_jobs=None, penalty='l2',
              power_t=0.5, random_state=42, shuffle=True, tol=0.001,
              validation_fraction=0.1, verbose=0, warm_start=False)

In [259]:
x_test = real_pipeline.fit_transform(x_test)

In [262]:
from sklearn.model_selection import cross_val_score
cross_val_score(sgd_clf, x_test, y_test, scoring = 'accuracy').mean()

0.7912396694214875

In [267]:
from sklearn.linear_model import LogisticRegression
log_reg = LogisticRegression()
log_reg.fit(x_train, y_train)
score = cross_val_score(log_reg, x_test, y_test, scoring = 'accuracy').mean()

/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)
/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression


In [268]:
print(score)

0.9750826446280992


### Accuracy = 97.508%